In [ ]:
# PROJECT MILESTONE 4 #

#Replace Headers
#Format data into a more readable format
#Identify outliers and bad data
#Find duplicates
#Fix casing or inconsistent values
#Conduct Fuzzy Matching

In [5]:
# load packages
import pandas as pd
import datetime as dt
import pandas_profiling as pp
from fuzzywuzzy import fuzz
import kaggle
from kaggle.api.kaggle_api_extended import KaggleApi

/Users/dragon/opt/anaconda3/lib/python3.8/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [4]:

import requests
df=[]
i=0
while True:
    if i==0:
        offset=""
    else:
        offset=f"%20offset%20{i}00"
    url=f"https://chronicdata.cdc.gov/resource/9cr5-2tt7.json?$query=select%20*%2C%20%3Aid{offset}%20limit%20100"
    temp=pd.read_json(requests.get(url).text)
    if temp.shape[0]>0:
        df.append(pd.read_json(requests.get(url).text))
        i+=1
    else:
        break
df=pd.concat(df)

In [5]:
df

locationid       year locationabbr locationdesc geographiclevel  \
0         1001       1999           AL      Autauga          County   
1         1001       2009           AL      Autauga          County   
2         1001       2006           AL      Autauga          County   
3         1001       2003           AL      Autauga          County   
4         1001       2000           AL      Autauga          County   
..         ...        ...          ...          ...             ...   
7        56045  2011-2018           WY       Weston          County   
8        56045  2005-2011           WY       Weston          County   
9        56045  1999-2005           WY       Weston          County   
10       56045  2005-2011           WY       Weston          County   
11       56045  2011-2018           WY       Weston          County   

   datasource                    class                   topic  data_value  \
0        NVSS  Cardiovascular Diseases                  Stroke        24.9   
1        NVSS  Cardiovascular Diseases                  Stroke        21.6   
2        NVSS  Cardiovascular Diseases                  Stroke        22.6   
3        NVSS  Cardiovascular Diseases                  Stroke        22.9   
4        NVSS  Cardiovascular Diseases                  Stroke        23.8   
..        ...                      ...                     ...         ...   
7        NVSS  Cardiovascular Diseases                  Stroke        -4.6   
8        NVSS  Cardiovascular Diseases                  Stroke       -12.8   
9        NVSS  Cardiovascular Diseases  Coronary Heart Disease        -7.4   
10       NVSS  Cardiovascular Diseases  Coronary Heart Disease       -18.3   
11       NVSS  Cardiovascular Diseases  Coronary Heart Disease         2.6   

   data_value_unit  ... confidence_limit_low  confidence_limit_high  \
0      per 100,000  ...                 18.1                   33.4   
1      per 100,000  ...                 17.1                   26.6   
2      per 100,000  ...                 18.3                   28.0   
3      per 100,000  ...                 18.4                   29.9   
4      per 100,000  ...                 17.5                   32.5   
..             ...  ...                  ...                    ...   
7                %  ...                -21.6                   18.0   
8                %  ...                -30.2                    5.6   
9                %  ...                -25.8                   19.9   
10               %  ...                -38.0                   -0.2   
11               %  ...                -18.6                   29.0   

    stratificationcategory1          stratification1 topicid      x_long  \
0                 Age group         Ages 35-64 years      T6  -86.642959   
1                 Age group         Ages 35-64 years      T6  -86.642959   
2                 Age group         Ages 35-64 years      T6  -86.642959   
3                 Age group         Ages 35-64 years      T6  -86.642959   
4                 Age group         Ages 35-64 years      T6  -86.642959   
..                      ...                      ...     ...         ...   
7                 Age group  Ages 65 years and older      T6 -104.567765   
8                 Age group  Ages 65 years and older      T6 -104.567765   
9                 Age group  Ages 65 years and older      T2 -104.567765   
10                Age group  Ages 65 years and older      T2 -104.567765   
11                Age group  Ages 65 years and older      T2 -104.567765   

        y_lat                 :id data_value_footnote_symbol  \
0   32.535306  row-3zud.q2q2.xwwp                        NaN   
1   32.535306  row-y3pn-6c95~pcrv                        NaN   
2   32.535306  row-9t3w.frfh~cu5f                        NaN   
3   32.535306  row-qnhb_jrva-k5yn                        NaN   
4   32.535306  row-q9hj_ejcq.7rj9                        NaN   
..        ...                 ...                        ...   


In [7]:
#  Data looks pretty good and saved in df dataframe
# Changing Name of the column
heart_health_ind_df=pd.DataFrame(df)
heart_health_ind_df.rename(columns={'locationabbr': 'LocationAbbreviation'}, inplace=True)
heart_health_ind_df

locationid       year LocationAbbreviation locationdesc geographiclevel  \
0         1001       1999                   AL      Autauga          County   
1         1001       2009                   AL      Autauga          County   
2         1001       2006                   AL      Autauga          County   
3         1001       2003                   AL      Autauga          County   
4         1001       2000                   AL      Autauga          County   
..         ...        ...                  ...          ...             ...   
7        56045  2011-2018                   WY       Weston          County   
8        56045  2005-2011                   WY       Weston          County   
9        56045  1999-2005                   WY       Weston          County   
10       56045  2005-2011                   WY       Weston          County   
11       56045  2011-2018                   WY       Weston          County   

   datasource                    class                   topic  data_value  \
0        NVSS  Cardiovascular Diseases                  Stroke        24.9   
1        NVSS  Cardiovascular Diseases                  Stroke        21.6   
2        NVSS  Cardiovascular Diseases                  Stroke        22.6   
3        NVSS  Cardiovascular Diseases                  Stroke        22.9   
4        NVSS  Cardiovascular Diseases                  Stroke        23.8   
..        ...                      ...                     ...         ...   
7        NVSS  Cardiovascular Diseases                  Stroke        -4.6   
8        NVSS  Cardiovascular Diseases                  Stroke       -12.8   
9        NVSS  Cardiovascular Diseases  Coronary Heart Disease        -7.4   
10       NVSS  Cardiovascular Diseases  Coronary Heart Disease       -18.3   
11       NVSS  Cardiovascular Diseases  Coronary Heart Disease         2.6   

   data_value_unit  ... confidence_limit_low  confidence_limit_high  \
0      per 100,000  ...                 18.1                   33.4   
1      per 100,000  ...                 17.1                   26.6   
2      per 100,000  ...                 18.3                   28.0   
3      per 100,000  ...                 18.4                   29.9   
4      per 100,000  ...                 17.5                   32.5   
..             ...  ...                  ...                    ...   
7                %  ...                -21.6                   18.0   
8                %  ...                -30.2                    5.6   
9                %  ...                -25.8                   19.9   
10               %  ...                -38.0                   -0.2   
11               %  ...                -18.6                   29.0   

    stratificationcategory1          stratification1 topicid      x_long  \
0                 Age group         Ages 35-64 years      T6  -86.642959   
1                 Age group         Ages 35-64 years      T6  -86.642959   
2                 Age group         Ages 35-64 years      T6  -86.642959   
3                 Age group         Ages 35-64 years      T6  -86.642959   
4                 Age group         Ages 35-64 years      T6  -86.642959   
..                      ...                      ...     ...         ...   
7                 Age group  Ages 65 years and older      T6 -104.567765   
8                 Age group  Ages 65 years and older      T6 -104.567765   
9                 Age group  Ages 65 years and older      T2 -104.567765   
10                Age group  Ages 65 years and older      T2 -104.567765   
11                Age group  Ages 65 years and older      T2 -104.567765   

        y_lat                 :id data_value_footnote_symbol  \
0   32.535306  row-3zud.q2q2.xwwp                        NaN   
1   32.535306  row-y3pn-6c95~pcrv                        NaN   
2   32.535306  row-9t3w.frfh~cu5f                        NaN   
3   32.535306  row-qnhb_jrva-k5yn                        NaN   
4   32.535306  row-q9hj_ejcq.7rj

In [10]:
#1 - Drop duplicates

heart_health_ind1 = heart_health_ind_df.drop_duplicates()
len_2 = heart_health_ind1.shape[0]


The above indicates duplicated values and the shape of the dataframe after dropping them.

In [12]:
#2 - Dataframe with no duplicate for further analysis
import pandas_profiling as pp
heart_health_ind_df1 = pd.DataFrame(heart_health_ind1)


pp.ProfileReport(heart_health_ind_df1)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [14]:
# 3 - Counting the type of heart decease
heart_health_ind_df1.topic.value_counts()

Coronary Heart Disease    144256
Stroke                    144256
Name: topic, dtype: int64

In [21]:
#4 - Filter

heart_health_ind_df1.query('locationid == 1001')

locationid       year LocationAbbreviation locationdesc geographiclevel  \
0         1001       1999                   AL      Autauga          County   
1         1001       2009                   AL      Autauga          County   
2         1001       2006                   AL      Autauga          County   
3         1001       2003                   AL      Autauga          County   
4         1001       2000                   AL      Autauga          County   
..         ...        ...                  ...          ...             ...   
87        1001  2005-2011                   AL      Autauga          County   
88        1001  1999-2005                   AL      Autauga          County   
89        1001  2005-2011                   AL      Autauga          County   
90        1001  1999-2005                   AL      Autauga          County   
91        1001  2005-2011                   AL      Autauga          County   

   datasource                    class                   topic  data_value  \
0        NVSS  Cardiovascular Diseases                  Stroke        24.9   
1        NVSS  Cardiovascular Diseases                  Stroke        21.6   
2        NVSS  Cardiovascular Diseases                  Stroke        22.6   
3        NVSS  Cardiovascular Diseases                  Stroke        22.9   
4        NVSS  Cardiovascular Diseases                  Stroke        23.8   
..        ...                      ...                     ...         ...   
87       NVSS  Cardiovascular Diseases  Coronary Heart Disease        -4.7   
88       NVSS  Cardiovascular Diseases                  Stroke       -18.9   
89       NVSS  Cardiovascular Diseases                  Stroke       -22.4   
90       NVSS  Cardiovascular Diseases  Coronary Heart Disease       -33.1   
91       NVSS  Cardiovascular Diseases  Coronary Heart Disease       -14.1   

   data_value_unit  ... confidence_limit_low  confidence_limit_high  \
0      per 100,000  ...                 18.1                   33.4   
1      per 100,000  ...                 17.1                   26.6   
2      per 100,000  ...                 18.3                   28.0   
3      per 100,000  ...                 18.4                   29.9   
4      per 100,000  ...                 17.5                   32.5   
..             ...  ...                  ...                    ...   
87               %  ...                -24.4                   25.0   
88               %  ...                -32.9                   -1.9   
89               %  ...                -36.7                   -4.0   
90               %  ...                -47.4                  -17.4   
91               %  ...                -31.2                    4.2   

    stratificationcategory1          stratification1 topicid     x_long  \
0                 Age group         Ages 35-64 years      T6 -86.642959   
1                 Age group         Ages 35-64 years      T6 -86.642959   
2                 Age group         Ages 35-64 years      T6 -86.642959   
3                 Age group         Ages 35-64 years      T6 -86.642959   
4                 Age group         Ages 35-64 years      T6 -86.642959   
..                      ...                      ...     ...        ...   
87                Age group         Ages 35-64 years      T2 -86.642959   
88                Age group  Ages 65 years and older      T6 -86.642959   
89                Age group  Ages 65 years and older      T6 -86.642959   
90                Age group  Ages 65 years and older      T2 -86.642959   
91                Age group  Ages 65 years and older      T2 -86.642959   

        y_lat                 :id data_value_footnote_symbol  \
0   32.535306  row-3zud.q2q2.xwwp                        NaN   
1   32.535306  row-y3pn-6c95~pcrv                        NaN   
2   32.535306  row-9t3w.frfh~cu5f                        NaN   
3   32.535306  row-qnhb_jrva-k5yn                        NaN   
4   32.535306  row-q9hj_ejcq.7rj9           

In [24]:
#5 - Group By

Year_confidence_limit_low_Group_Count = (heart_health_ind_df1.groupby('year').agg(count = ('confidence_limit_low', 'size')))

In [25]:
Year_confidence_limit_low_Group_Count

count
year            
1999         933
2000         938
2001         950
2002         931
2003         906
2004         928
2005         927
2006         912
2007         921
2008         908
2009         919
2010         931
2011         925
2012         942
2013         940
2014         922
2015         936
2016         956
2017         938
2018         937
1999       11611
1999-2005  12544
2000       11606
2001       11594
2002       11613
2003       11638
2004       11616
2005       11617
2005-2011  12544
2006       11632
2007       11623
2008       11636
2009       11625
2010       11613
2011       11619
2011-2018  12544
2012       11602
2013       11604
2014       11622
2015       11608
2016       11588
2017       11606
2018       11607

In [1]:
kaggle datasets download -d sulianova/cardiovascular-disease-dataset

SyntaxError: invalid syntax (<ipython-input-1-dc28185a7100>, line 1)

In [2]:
kaggle datasets download -d charankakaraparthi/heart-dissease 

SyntaxError: invalid syntax (<ipython-input-2-57c2ad922bca>, line 1)

In [3]:
import kaggle

In [4]:
kaggle datasets download -d charankakaraparthi/heart-dissease

SyntaxError: invalid syntax (<ipython-input-4-7ae5a69ce180>, line 1)

In [6]:
kaggle datasets download -d charankakaraparthi/heart-dissease

SyntaxError: invalid syntax (<ipython-input-6-7ae5a69ce180>, line 1)

In [7]:
kaggleapi datasets download -d charankakaraparthi/heart-dissease

SyntaxError: invalid syntax (<ipython-input-7-7e4c02b23fd2>, line 1)

In [8]:
pip install kaggle

Note: you may need to restart the kernel to use updated packages.


In [ ]:
kaggleapi datasets download -d charankakaraparthi/heart-dissease